In [16]:
import ibis
from ibis import _
import streamlit as st
import ibis.expr.datatypes as dt  # Make sure to import the necessary module


conn = ibis.duckdb.connect(extensions=["spatial"])

# pres = conn.read_csv("sources-president.csv")
county = conn.read_csv("countypres_2000-2020.csv")
votes = conn.read_parquet("vote.parquet")

# Getting party affiliations for counties

In [ ]:
filtered = county.filter((_.mode == "TOTAL") & (_.totalvotes > 0))

# Find the winning party for each year, state, and county
most_votes = (
    filtered
    .group_by(['year', 'state_po', 'county_name', 'party'])
    .aggregate(winning_votes=_.candidatevotes.sum())
)

# For each year, state, and county, select the party with the highest total votes
winning_party = (
    most_votes
    .group_by('year', 'state_po', 'county_name')
    .aggregate(
        max_votes=_.winning_votes.max(),  # Max votes in this group
    )
    .join(
        most_votes,
        ["year","state_po","county_name",most_votes['winning_votes'] == _.max_votes],
        how='inner'
    )
    .select("year","state_po","county_name",most_votes['party'].name('current_party')
    )
)

# Self-join to get the previous year's winning party
previous_year = winning_party.view()

joined = (
    winning_party
    .join(
        previous_year, ["county_name","state_po",winning_party['year'] == previous_year['year'] + 4],
        how='left'
    )
    .rename(state_id = "state_po")
    .mutate(key = _.county_name + ibis.literal(" COUNTY-") + _.state_id)
    .select("year","key","current_party",previous_year['current_party'].name('previous_party'))
)

county_parties = joined.filter(_.year >2000).order_by("year")

print(county_parties.execute())

In [ ]:
df = (votes
        .mutate(key = _.key.upper())
        .filter(_.jurisdiction == "Municipal")
        .join(county_parties, ["key","year"],how='inner'
        )
        .cast({"geometry": "geometry"})
)

In [30]:
import subprocess
import os
from huggingface_hub import HfApi, login
import streamlit as st

login(st.secrets["HF_TOKEN"])
# api = HfApi(add_to_git_credential=False)
api = HfApi()

def hf_upload(file, repo_id):
    info = api.upload_file(
            path_or_fileobj=file,
            path_in_repo=file,
            repo_id=repo_id,
            repo_type="dataset",
        )
def generate_pmtiles(input_file, output_file, max_zoom=12):
    # Ensure Tippecanoe is installed
    if subprocess.call(["which", "tippecanoe"], stdout=subprocess.DEVNULL) != 0:
        raise RuntimeError("Tippecanoe is not installed or not in PATH")

    # Construct the Tippecanoe command
    command = [
        "tippecanoe",
        "-o", output_file,
        "-zg",
        "--extend-zooms-if-still-dropping",
        "--force",
        "--projection", "EPSG:4326",  
        input_file
    ]

    # Run Tippecanoe
    try:
        subprocess.run(command, check=True)
        print(f"Successfully generated PMTiles file: {output_file}")
    except subprocess.CalledProcessError as e:
        print(f"Error running Tippecanoe: {e}")



The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /home/rstudio/.cache/huggingface/token
Login successful


In [ ]:
gdf= df.execute()
gdf = gdf.set_crs("EPSG:4326")

# gdf.to_parquet("county_parties.parquet")
# hf_upload("county_parties.parquet", "boettiger-lab/landvote")

# gdf.to_file("county_parties.geojson")
# hf_upload("county_parties.geojson", "boettiger-lab/landvote")

# generate_pmtiles("county_parties.geojson", "county_parties.pmtiles")
# hf_upload("county_parties.pmtiles", "boettiger-lab/landvote")


# Checking map

In [ ]:
import leafmap.maplibregl as leafmap
m = leafmap.Map(style="positron")


url_states = "https://huggingface.co/datasets/boettiger-lab/landvote/resolve/main/county_parties.pmtiles"

outcome = [
      'match',
      ['get', 'Status'], 
      "Pass", '#2E865F',
      "Fail", '#FF3300', 
      '#ccc'
    ]
paint_states = {"fill-color": outcome, 
         # "fill-opacity": 0.2,
        }
style_states = {
    "layers": [
        {
            "id": "county_parties",
            "source": "county_parties",
            "source-layer": "county_parties",
            "type": "fill",
            "filter": [
                "==",
                ["get", "year"],
                2008,
            ],  # only show buildings with height info
            "paint": paint_states
        },
    ],
}

m.add_pmtiles(
    url_states,
    style=style_states,
    visible=True,
    opacity=0.4,
    tooltip=True,
    fit_bounds=False,
)

m


# Getting Municipals 

In [ ]:

localities_boundaries = "us_localities.parquet"
locality = conn.read_parquet(localities_boundaries)
landvote = conn.read_csv("landvote.csv")

#needed to redo this, since I didn't save county in "votes.parquet". 
vote_local = (landvote
                .filter(_["Jurisdiction Type"] == "Municipal")
                .rename(city = "Jurisdiction Name", state_id = "State")
                .mutate(key = _.city + ibis.literal('-') + _.state_id)
                .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
                .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
                .mutate(log_amount=_.amount_n.log())
                .mutate(year=_['Date'].year().cast('int32'))
                .mutate(
                    yes=ibis.case()
                        .when(_.yes.isin(['Pass', 'None','Fail']), None)  # Handle non-numeric cases
                        .when(_.yes.notnull(), (_.yes.replace('%', '').cast('float').round(2).cast(dt.float64)).cast(dt.string) + '%')  # Convert valid percentages and add %
                        .else_(None)  # Default to None for other cases
                        .end()
                )
              .mutate(log_amount = _.log_amount.round(4))
                .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
                )

# getting the county parties for each municipal  
df_municipals = (locality 
            .mutate(key_municipal = _.name + ibis.literal('-') + _.state_id) 
            .mutate(key = (_.county + ibis.literal('-') + _.state_id).upper()) 
            .select('key', 'geometry','key_municipal','name')
            .right_join(vote_local, [_.key_municipal == vote_local["key"]])
            .mutate(jurisdiction = ibis.literal("Municipal"))
            .cast({"geometry": "geometry"})
            .mutate(geometry = _.geometry.buffer(.07))
            .join(county_parties, ["key","year"],how='inner')
            .rename(county = "key")
            .rename(key = "key_municipal")
            .select('key','geometry','Status','yes','year','amount','log_amount','jurisdiction','current_party','previous_party')
           )


gdf_municipals = df_municipals.execute()
gdf_municipals = gdf_municipals.set_crs("EPSG:4326")
gdf_municipals


# gdf_municipals.to_parquet("municipal_parties.parquet")
# hf_upload("municipal_parties.parquet", "boettiger-lab/landvote")

# gdf_municipals.to_file("municipal_parties.geojson")
# hf_upload("municipal_parties.geojson", "boettiger-lab/landvote")

# generate_pmtiles("municipal_parties.geojson", "municipal_parties.pmtiles")
# hf_upload("municipal_parties.pmtiles", "boettiger-lab/landvote")


# Get States

In [28]:
states = (conn
          .read_csv("1976-2020-president.csv")
          .filter(_. year >=2000)
         )
# states.execute()

In [18]:
# filtered = county.filter((_.mode == "TOTAL") & (_.totalvotes > 0))

# Find the winning party for each year, state, and county
most_votes= (
    states
    .group_by(['year', 'state_po', 'party_simplified'])
    .aggregate(winning_votes=_.candidatevotes.sum())
)

# For each year, state, and county, select the party with the highest total votes
winning_party = (
    most_votes
    .group_by('year', 'state_po')
    .aggregate(
        max_votes=_.winning_votes.max(),  # Max votes in this group
    )
    .join(
        most_votes,
        ["year","state_po",most_votes['winning_votes'] == _.max_votes],
        how='inner'
    )
    .select("year","state_po",most_votes['party_simplified'].name('current_party')
    )
)

# Self-join to get the previous year's winning party
previous_year = winning_party.view()

joined = (
    winning_party
    .join(
        previous_year, ["state_po",winning_party['year'] == previous_year['year'] + 4],
        how='left'
    )
    .rename(key = "state_po")
    # .mutate(key = _.county_name + ibis.literal(" COUNTY-") + _.state_id)
    .select("year","key","current_party",previous_year['current_party'].name('previous_party'))
)

state_parties = joined.filter(_.year >2000).order_by("year")

print(state_parties.execute())

     year key current_party previous_party
0    2004  HI      DEMOCRAT       DEMOCRAT
1    2004  ME      DEMOCRAT       DEMOCRAT
2    2004  NJ      DEMOCRAT       DEMOCRAT
3    2004  NM    REPUBLICAN       DEMOCRAT
4    2004  ND    REPUBLICAN     REPUBLICAN
..    ...  ..           ...            ...
250  2020  VT      DEMOCRAT       DEMOCRAT
251  2020  AL    REPUBLICAN     REPUBLICAN
252  2020  IA    REPUBLICAN     REPUBLICAN
253  2020  SD    REPUBLICAN     REPUBLICAN
254  2020  GA      DEMOCRAT     REPUBLICAN

[255 rows x 4 columns]


In [31]:
# state_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-state-territory.parquet"
states = conn.read_parquet("vote_states.parquet")

df_states = (states
        .mutate(key = _.key.upper())
        # .filter(_.jurisdiction == "Municipal")
        .join(state_parties, ["key","year"],how='inner'
        )
        .cast({"geometry": "geometry"})
)

gdf_states = df_states.execute()
gdf_states = gdf_states.set_crs("EPSG:4326")
gdf_states


gdf_states.to_parquet("states_parties.parquet")
hf_upload("states_parties.parquet", "boettiger-lab/landvote")

gdf_states.to_file("states_parties.geojson")
hf_upload("states_parties.geojson", "boettiger-lab/landvote")

generate_pmtiles("states_parties.geojson", "states_parties.pmtiles")
hf_upload("states_parties.pmtiles", "boettiger-lab/landvote")


states_parties.parquet:   0%|          | 0.00/2.36M [00:00<?, ?B/s]

For layer 0, using name "states_parties"
12 features, 833591 bytes of geometry and attributes, 542 bytes of string pool, 0 bytes of vertices, 0 bytes of nodes
Choosing a maxzoom of -z0 for features typically 7514540 feet (2290432 meters) apart, and at least 2073685 feet (632060 meters) apart
Choosing a maxzoom of -z10 for resolution of about 376 feet (114 meters) within features
  99.9%  10/271/383  


Successfully generated PMTiles file: states_parties.pmtiles
